In [1]:
#! pip install ultralytics 
#! pip install psycopg2
from PIL import Image
import numpy as np
import cv2
import matplotlib.pyplot as plt
import os
from ultralytics import YOLO
import psycopg2
import im_utils
import db_ops
import pandas as pd

import boto3
s3_client = boto3.client('s3')

Connecting to the PostgreSQL database...
Connection successful


#### Get the full list of OLM images

In [2]:
objects = s3_client.list_objects_v2(Bucket='olm-processed-s3')


session = boto3.Session()

s3 = session.resource('s3')

my_bucket = s3.Bucket('olm-processed-s3')

scaled_pics = [objects.key.split('/')[-1].split('.')[0]  for objects in my_bucket.objects.filter(Prefix="scaled/")]

In [3]:
scaled_pics[:3]

['tTyxAD9TsRwRm6yHD8TZrmin76zbW08A9NXCaxz9',
 '18RfT51ZmG4CbSBoRLQKOSFB5J6p8Hc1XX3qosy6',
 '2ObwUbTXkBbQKOmW0xXLhf6msJCqk9G4pQDyHzpd']

In [4]:
query = f'''
SELECT DISTINCT ON (i.image_id)
	 i.s3_uri AS uri
	, i.image_id as image_id
	, b.brand_id as brand_id 
	, ci.cat_id as cat_id
FROM image AS i 
	LEFT JOIN brand_image AS bi
		ON i.image_id = bi.image_id
	LEFT JOIN brand as b
		ON b.brand_id = bi.brand_id 
	LEFT JOIN category_image as ci
		ON i.image_id = ci.image_id
ORDER BY i.image_id	;
'''
image_uri = db_ops.select_to_pandas(query, True, True)

/home/ubuntu/workspace/litter-imagery-brand-recognition/db_ops.py:57: UserWarning: pandas only supports SQLAlchemy connectable (engine/connection) or database string URI or sqlite3 DBAPI2 connection. Other DBAPI2 objects are not tested. Please consider using SQLAlchemy.
  df = pd.read_sql_query(query, connection)


In [5]:
# Replace the missing brand and category id with the right placeholders
image_uri['brand_id'] = image_uri['brand_id'].fillna(value = 111).astype(int)
image_uri['cat_id'] = image_uri['cat_id'].fillna(value = 20).astype(int)
image_uri['file'] = image_uri['uri'].apply(lambda x: x.split('/')[-1].split('.')[0])

In [6]:
len(image_uri)

27388

In [7]:
# Replace the missing brand and category id with the right placeholdersFilter out the images that has already been processed
image_uri = image_uri[~image_uri['file'].isin(scaled_pics)]


In [8]:
len(image_uri)

12269

#### Copy the image from the original S3, resize it, save to the procesed S3

In [9]:
for i in range(len(image_uri)):
    print('-'*30)
    try:
        original_im_uri = image_uri['uri'].iloc[i]
        tmp_im_folder = '/home/ubuntu/temp-images'
        im_file = original_im_uri.split('/')[-1]
        scaled_im_uri = original_im_uri.replace('-pics-s3', '-processed-s3/scaled').split('.')[0] + '.jpg'
        scaled_im_local_path = os.path.join(tmp_im_folder, 'scaled', im_file.split('.')[0] + '.jpg')
        
        os.system(f"aws s3 cp {original_im_uri} {tmp_im_folder}")  
        image_original = cv2.imread(tmp_im_folder+'/'+im_file)
        image_scaled = im_utils.ScaleImage(image_original, width = 640)
        print(f'Scaled im shape {image_scaled.shape}')
        cv2.imwrite(scaled_im_local_path, image_scaled)
        os.system(f"aws s3 cp {scaled_im_local_path} {scaled_im_uri}")
        os.system(f"find ~/temp-images/ -maxdepth 2 -type f -delete")
    except Exception as e:
        print(e)

------------------------------


fatal error: An error occurred (404) when calling the HeadObject operation: Key "2020/05/07/MjAyMDowNTowNyAxNTo0OToxNQ%3D%3D.jpg" does not exist
[ WARN:0@45.577] global loadsave.cpp:241 findDecoder imread_('/home/ubuntu/temp-images/MjAyMDowNTowNyAxNTo0OToxNQ%3D%3D.jpg'): can't open/read file: check file path/integrity


'NoneType' object has no attribute 'shape'
------------------------------


fatal error: An error occurred (404) when calling the HeadObject operation: Key "2020/05/07/MjAyMDowNTowNyAxNjowMjoyNA%3D%3D.jpg" does not exist
[ WARN:0@46.131] global loadsave.cpp:241 findDecoder imread_('/home/ubuntu/temp-images/MjAyMDowNTowNyAxNjowMjoyNA%3D%3D.jpg'): can't open/read file: check file path/integrity


'NoneType' object has no attribute 'shape'
------------------------------


...

'NoneType' object has no attribute 'shape'
------------------------------
download: s3://olm-pics-s3/2023/06/27/OL9Mmmol1Os4toeAffaAmlqZJL5z5GWlpOlnmqUI.heic to ../../temp-images/OL9Mmmol1Os4toeAffaAmlqZJL5z5GWlpOlnmqUI.heic
Scaled im shape (853, 640, 3)
upload: ../../temp-images/scaled/OL9Mmmol1Os4toeAffaAmlqZJL5z5GWlpOlnmqUI.jpg to s3://olm-processed-s3/scaled/2023/06/27/OL9Mmmol1Os4toeAffaAmlqZJL5z5GWlpOlnmqUI.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/27/G8knsa2whvl0gg4UTBUFVBylIiGZ4DmpwVcAuet1.heic to ../../temp-images/G8knsa2whvl0gg4UTBUFVBylIiGZ4DmpwVcAuet1.heic
Scaled im shape (853, 640, 3)
upload: ../../temp-images/scaled/G8knsa2whvl0gg4UTBUFVBylIiGZ4DmpwVcAuet1.jpg to s3://olm-processed-s3/scaled/2023/06/27/G8knsa2whvl0gg4UTBUFVBylIiGZ4DmpwVcAuet1.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/27/O5j8rr2nqpc8Vu9bVnXoutly2bK4lvi4B7wnJj07.heic to ../../temp-images/O5j8rr2nqpc8Vu9bVnXoutly2bK4lvi4B7wnJj07.heic
Scaled im shape (85

fatal error: An error occurred (404) when calling the HeadObject operation: Key "2023/06/29/vkCa0iHD6Ucn1MRuj0qx5KZPck3dhRtWC1EYAlqF.heic" does not exist
[ WARN:0@21265.765] global loadsave.cpp:241 findDecoder imread_('/home/ubuntu/temp-images/vkCa0iHD6Ucn1MRuj0qx5KZPck3dhRtWC1EYAlqF.heic'): can't open/read file: check file path/integrity


'NoneType' object has no attribute 'shape'
------------------------------
download: s3://olm-pics-s3/2023/06/29/eglYNW691lwP1ievrnKcpdLnVzZulkNeXCdzaNUM.heic to ../../temp-images/eglYNW691lwP1ievrnKcpdLnVzZulkNeXCdzaNUM.heic
Scaled im shape (853, 640, 3)
upload: ../../temp-images/scaled/eglYNW691lwP1ievrnKcpdLnVzZulkNeXCdzaNUM.jpg to s3://olm-processed-s3/scaled/2023/06/29/eglYNW691lwP1ievrnKcpdLnVzZulkNeXCdzaNUM.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/29/bvltpfqvGqVY5h4Iu0GLAoWu1D73zbmSzXvq4DIT.heic to ../../temp-images/bvltpfqvGqVY5h4Iu0GLAoWu1D73zbmSzXvq4DIT.heic
Scaled im shape (853, 640, 3)
upload: ../../temp-images/scaled/bvltpfqvGqVY5h4Iu0GLAoWu1D73zbmSzXvq4DIT.jpg to s3://olm-processed-s3/scaled/2023/06/29/bvltpfqvGqVY5h4Iu0GLAoWu1D73zbmSzXvq4DIT.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/29/te7RiNYhzyTZjFcUsJGd3yG2phjzWFSfukoTOY0L.heic to ../../temp-images/te7RiNYhzyTZjFcUsJGd3yG2phjzWFSfukoTOY0L.heic
Scaled im shape (85

fatal error: An error occurred (404) when calling the HeadObject operation: Key "2023/06/29/fj0pTqYeyCA5IlbrU7mjcB6Wp55mQh3OJzhs6jzn.heic" does not exist
[ WARN:0@21296.881] global loadsave.cpp:241 findDecoder imread_('/home/ubuntu/temp-images/fj0pTqYeyCA5IlbrU7mjcB6Wp55mQh3OJzhs6jzn.heic'): can't open/read file: check file path/integrity


'NoneType' object has no attribute 'shape'
------------------------------
download: s3://olm-pics-s3/2023/06/29/sMXqAfVASApmZO7LrP6BHBznZ15kYVDOAqsPV8Xz.heic to ../../temp-images/sMXqAfVASApmZO7LrP6BHBznZ15kYVDOAqsPV8Xz.heic
Scaled im shape (853, 640, 3)
upload: ../../temp-images/scaled/sMXqAfVASApmZO7LrP6BHBznZ15kYVDOAqsPV8Xz.jpg to s3://olm-processed-s3/scaled/2023/06/29/sMXqAfVASApmZO7LrP6BHBznZ15kYVDOAqsPV8Xz.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/29/2QyzUjdQYU5UjHd9kcPSxuH2RPQfXb1gHZbmtNVv.heic to ../../temp-images/2QyzUjdQYU5UjHd9kcPSxuH2RPQfXb1gHZbmtNVv.heic
Scaled im shape (480, 640, 3)
upload: ../../temp-images/scaled/2QyzUjdQYU5UjHd9kcPSxuH2RPQfXb1gHZbmtNVv.jpg to s3://olm-processed-s3/scaled/2023/06/29/2QyzUjdQYU5UjHd9kcPSxuH2RPQfXb1gHZbmtNVv.jpg
------------------------------
download: s3://olm-pics-s3/2023/06/29/3y4kZYwTtlvRTdzVVuoHaT1P2PFFfF0PL610cqM8.heic to ../../temp-images/3y4kZYwTtlvRTdzVVuoHaT1P2PFFfF0PL610cqM8.heic
Scaled im shape (85